# Social Vulnerability Ireland - Copernicus data
Processing of the Copernicus data into census output areas

## Environment

### R Libraries
Any required R libraries are imported into the kernal:

In [1]:
# Load R libraries
if(!require("pacman"))
    install.packages("pacman")

p_load("sf", "terra", "exactextractr")

print("Loaded Packages:")
p_loaded()

Loading required package: pacman



[1] "Loaded Packages:"


[1] "exactextractr" "terra"         "sf"            "pacman"

In [2]:
### Output directory

In [3]:
# create the pipeline directory if it does not exist
pipeline_dir <- file.path("../..","2_pipeline","Ireland","1b_Copernicus","2022")
if(!dir.exists(pipeline_dir)){
    dir.create(pipeline_dir, recursive = TRUE)
    print(paste0(pipeline_dir, " created"))
}

# set country variable which is used within the output filename
country <- "Ireland"

## Process

In [4]:
# Copernicus data folder
copernicus_data_path <- "../../0_data/Copernicus/Ireland"

# High resolution layers - IMPERVIOUSNESS, TREE COVER DENSITY
datasets <- c("IMD","TCD")

# census output areas
census_areas <- st_read("../../0_data/boundaries/Ireland/census_small_areas/2022/SMALL_AREA_2022.shp")

Reading layer `SMALL_AREA_2022' from data source 
  `/Cities/0_data/boundaries/Ireland/census_small_areas/2022/SMALL_AREA_2022.shp' 
  using driver `ESRI Shapefile'
Simple feature collection with 18919 features and 28 fields
Geometry type: MULTIPOLYGON
Dimension:     XY
Bounding box:  xmin: 417471.5 ymin: 519663.7 xmax: 734481.1 ymax: 966896.3
Projected CRS: IRENET95 / Irish Transverse Mercator


In [5]:
# need to join copernicus tiles together
for(dataset in datasets){
    print(paste0("Processing: ", dataset))
    flush.console()

    # export mosaic filepath
    mosaic_output_file <- paste0(pipeline_dir, "/", country, "_", dataset, ".tif")

    # have the tiles been joined together already?
    is_mosaic_created <- file.exists(mosaic_output_file)

    if(is_mosaic_created){
        print(paste0(mosaic_output_file, " already created"))
        flush.console()
    } else {
        # Join the tiles together and export it
        # Get the files
        tiles <- list.files(copernicus_data_path, full.names = TRUE, recursive = TRUE, pattern=paste0(".*", dataset, ".*\\.tif$"))  

        # Create an image catalog
        ic <- terra::sprc(lapply(tiles, rast))

        # Mosic the tiles
        icMosaic <- mosaic(ic, filename = mosaic_output_file, fun="max", overwrite=TRUE)
        #icMosaic <- merge(ic, filename = mosaic_output_file, overwrite=TRUE) # quicker

        print(paste0(mosaic_output_file, " created"))
    }   
}

[1] "Processing: IMD"
[1] "../../2_pipeline/Ireland/1b_Copernicus/2022/Ireland_IMD.tif already created"
[1] "Processing: TCD"
[1] "../../2_pipeline/Ireland/1b_Copernicus/2022/Ireland_TCD.tif already created"


In [6]:
Sys.time()
census_areas_impervious <- census_areas

# Impervious surface
copRaster <- rast(paste0(pipeline_dir, "/", country, "_", "IMD", ".tif"))

# calculate the area of the raster cell (m2)
cellArea <- res(copRaster)[1]*res(copRaster)[2]

# calculate the number of cells within each output area
census_areas_impervious$cell_area_m2 <- exact_extract(copRaster, census_areas_impervious, 'count', coverage_area = TRUE, progress = TRUE)

# calculate the area of each output area that is impervious
census_areas_impervious$imp_area_m2 <- exact_extract(copRaster, census_areas_impervious, 'sum', progress = TRUE)

# calculate the percentage of each output area that is impervious
census_areas_impervious$imp_percent <- round((census_areas_impervious$imp_area_m2/census_areas_impervious$cell_area_m2)*100, 3)

# calculate Z score
census_areas_impervious$impervious <- scale(census_areas_impervious$imp_percent)

head(census_areas_impervious)
Sys.time()

[1] "2025-03-13 15:40:39 GMT"

Warning message in .local(x, y, ...):
“Polygons transformed to raster CRS (EPSG:3035)”
Cannot preload entire working area of 1395265641 cells with max_cells_in_memory = 3e+07. Raster values will be read for each feature individually.




 |======================================================================| 100%

Warning message in .local(x, y, ...):
“Polygons transformed to raster CRS (EPSG:3035)”
Cannot preload entire working area of 1395265641 cells with max_cells_in_memory = 3e+07. Raster values will be read for each feature individually.




 |======================================================================| 100%

Registered S3 method overwritten by 'geojsonsf':
  method        from   
  print.geojson geojson



OBJECTID SA_GUID_20                          
1 1        4c07d11e-0a4f-851d-e053-ca3ca8c0ca7f
2 2        4c07d11e-0a3a-851d-e053-ca3ca8c0ca7f
3 3        4c07d11e-0a4e-851d-e053-ca3ca8c0ca7f
4 4        4c07d11e-0a25-851d-e053-ca3ca8c0ca7f
5 5        4c07d11e-0a57-851d-e053-ca3ca8c0ca7f
6 6        4c07d11e-2df2-851d-e053-ca3ca8c0ca7f
  SA_GUID__1                           SA_PUB2011 SA_PUB2016 SA_PUB2022
1 4c07d11e-0a4f-851d-e053-ca3ca8c0ca7f 017010016  017010016  017010016 
2 4c07d11e-0a3a-851d-e053-ca3ca8c0ca7f 017010046  017010046  017010046 
3 4c07d11e-0a4e-851d-e053-ca3ca8c0ca7f 017010037  017010037  017010037 
4 4c07d11e-0a25-851d-e053-ca3ca8c0ca7f 017010005  017010005  017010005 
5 4c07d11e-0a57-851d-e053-ca3ca8c0ca7f 017010036  017010036  017010036 
6 4c07d11e-2df2-851d-e053-ca3ca8c0ca7f 017010009  017010009  017010009 
  SA_GEOGID_ SA_CHANGE_ SA_URBAN_A SA_URBAN_1 geometry                       ⋯
1 A017010016 0          1          Carlow     MULTIPOLYGON (((673146.5 67... ⋯
2 A017010046 4          1          Carlow     MULTIPOLYGON (((673956.3 67... ⋯
3 A017010037 0          1          Carlow     MULTIPOLYGON (((673720.6 67... ⋯
4 A017010005 0          1          Carlow     MULTIPOLYGON (((671923.3 67... ⋯
5 A017010036 0          1          Carlow     MULTIPOLYGON (((673711.8 67... ⋯
6 A017010009 4          1          Carlow     MULTIPOLYGON (((673488.5 67... ⋯
  COUNTY_ENG COUNTY_GAE  CSO_LEA SHAPE_Leng SHAPE_Area
1 CARLOW     Ceatharlach CARLOW  2123.346   204944.2  
2 CARLOW     Ceatharlach CARLOW  2891.271   288225.4  
3 CARLOW     Ceatharlach CARLOW  2436.986   208426.9  
4 CARLOW     Ceatharlach CARLOW  2887.091   348798.6  
5 CARLOW     Ceatharlach CARLOW  2844.410   429349.1  
6 CARLOW     Ceatharlach CARLOW  1058.290    59299.2  
  geometry                       cell_area_m2 imp_area_m2 imp_percent
1 MULTIPOLYGON (((673146.5 67... 204991.3      75945.95   37.048     
2 MULTIPOLYGON (((673956.3 67... 288290.4      57333.25   19.887     
3 MULTIPOLYGON (((673720.6 67... 208474.4      69274.20   33.229     
4 MULTIPOLYGON (((671923.3 67... 348880.3     109519.96   31.392     
5 MULTIPOLYGON (((673711.8 67... 429446.9     209251.55   48.726     
6 MULTIPOLYGON (((673488.5 67...  59312.7      18759.59   31.628     
  impervious
1  0.4175754
2 -0.2955289
3  0.2588815
4  0.1825472
5  0.9028403
6  0.1923539

[1] "2025-03-13 15:52:17 GMT"

In [7]:
# output the impervious data as a geojson
st_write(census_areas_impervious, file.path(pipeline_dir, "census_areas_IMD.geojson"), delete_dsn = TRUE)

Deleting source `../../2_pipeline/Ireland/1b_Copernicus/2022/census_areas_IMD.geojson' using driver `GeoJSON'
Writing layer `census_areas_IMD' to data source 
  `../../2_pipeline/Ireland/1b_Copernicus/2022/census_areas_IMD.geojson' using driver `GeoJSON'
Writing 18919 features with 32 fields and geometry type Multi Polygon.


In [8]:
Sys.time()
census_areas_tree_cover <- census_areas

# TREE COVER DENSITY
# cell size = 100 m2, therefore a percentage value directly equals m2, i.e. 100% coverage = 100 m2 area of impervious surface
copRaster <- rast(paste0(pipeline_dir, "/", country, "_", "TCD", ".tif"))

# calculate the area of the raster cell (m2)
cellArea <- res(copRaster)[1]*res(copRaster)[2]

# calculate the number of cells within each output area
census_areas_tree_cover$cell_area_m2 <- exact_extract(copRaster, census_areas_tree_cover, 'count', coverage_area = TRUE, progress = TRUE)

# calculate the area of each output area that has tree cover
census_areas_tree_cover$tcd_area_m2 <- exact_extract(copRaster, census_areas_tree_cover, 'sum', progress = TRUE)

# calculate the percentage of each output area that has tree cover
census_areas_tree_cover$tcd_percent <- round((census_areas_tree_cover$tcd_area_m2/census_areas_tree_cover$cell_area_m2)*100, 3)

# calculate Z score
census_areas_tree_cover$tree_cover_density <- -scale(census_areas_tree_cover$tcd_percent)

head(census_areas_tree_cover)
Sys.time()

[1] "2025-03-13 15:53:31 GMT"

Warning message in .local(x, y, ...):
“Polygons transformed to raster CRS (EPSG:3035)”
Cannot preload entire working area of 1395265641 cells with max_cells_in_memory = 3e+07. Raster values will be read for each feature individually.




 |======================================================================| 100%

Warning message in .local(x, y, ...):
“Polygons transformed to raster CRS (EPSG:3035)”
Cannot preload entire working area of 1395265641 cells with max_cells_in_memory = 3e+07. Raster values will be read for each feature individually.




 |======================================================================| 100%

OBJECTID SA_GUID_20                          
1 1        4c07d11e-0a4f-851d-e053-ca3ca8c0ca7f
2 2        4c07d11e-0a3a-851d-e053-ca3ca8c0ca7f
3 3        4c07d11e-0a4e-851d-e053-ca3ca8c0ca7f
4 4        4c07d11e-0a25-851d-e053-ca3ca8c0ca7f
5 5        4c07d11e-0a57-851d-e053-ca3ca8c0ca7f
6 6        4c07d11e-2df2-851d-e053-ca3ca8c0ca7f
  SA_GUID__1                           SA_PUB2011 SA_PUB2016 SA_PUB2022
1 4c07d11e-0a4f-851d-e053-ca3ca8c0ca7f 017010016  017010016  017010016 
2 4c07d11e-0a3a-851d-e053-ca3ca8c0ca7f 017010046  017010046  017010046 
3 4c07d11e-0a4e-851d-e053-ca3ca8c0ca7f 017010037  017010037  017010037 
4 4c07d11e-0a25-851d-e053-ca3ca8c0ca7f 017010005  017010005  017010005 
5 4c07d11e-0a57-851d-e053-ca3ca8c0ca7f 017010036  017010036  017010036 
6 4c07d11e-2df2-851d-e053-ca3ca8c0ca7f 017010009  017010009  017010009 
  SA_GEOGID_ SA_CHANGE_ SA_URBAN_A SA_URBAN_1 geometry                       ⋯
1 A017010016 0          1          Carlow     MULTIPOLYGON (((673146.5 67... ⋯
2 A017010046 4          1          Carlow     MULTIPOLYGON (((673956.3 67... ⋯
3 A017010037 0          1          Carlow     MULTIPOLYGON (((673720.6 67... ⋯
4 A017010005 0          1          Carlow     MULTIPOLYGON (((671923.3 67... ⋯
5 A017010036 0          1          Carlow     MULTIPOLYGON (((673711.8 67... ⋯
6 A017010009 4          1          Carlow     MULTIPOLYGON (((673488.5 67... ⋯
  COUNTY_ENG COUNTY_GAE  CSO_LEA SHAPE_Leng SHAPE_Area
1 CARLOW     Ceatharlach CARLOW  2123.346   204944.2  
2 CARLOW     Ceatharlach CARLOW  2891.271   288225.4  
3 CARLOW     Ceatharlach CARLOW  2436.986   208426.9  
4 CARLOW     Ceatharlach CARLOW  2887.091   348798.6  
5 CARLOW     Ceatharlach CARLOW  2844.410   429349.1  
6 CARLOW     Ceatharlach CARLOW  1058.290    59299.2  
  geometry                       cell_area_m2 tcd_area_m2 tcd_percent
1 MULTIPOLYGON (((673146.5 67... 204991.3       202.7830  0.099      
2 MULTIPOLYGON (((673956.3 67... 288290.4       961.1264  0.333      
3 MULTIPOLYGON (((673720.6 67... 208474.4       968.9902  0.465      
4 MULTIPOLYGON (((671923.3 67... 348880.3     26616.5039  7.629      
5 MULTIPOLYGON (((673711.8 67... 429446.9     11372.1279  2.648      
6 MULTIPOLYGON (((673488.5 67...  59312.7       107.7513  0.182      
  tree_cover_density
1  0.7831503        
2  0.7459016        
3  0.7248895        
4 -0.4154939        
5  0.3773941        
6  0.7699382

[1] "2025-03-13 16:07:43 GMT"

## Export

In [9]:
# output the tree cover density data as a geojson
st_write(census_areas_tree_cover, file.path(pipeline_dir, "census_areas_TCD.geojson"), delete_dsn = TRUE)

Deleting source `../../2_pipeline/Ireland/1b_Copernicus/2022/census_areas_TCD.geojson' using driver `GeoJSON'
Writing layer `census_areas_TCD' to data source 
  `../../2_pipeline/Ireland/1b_Copernicus/2022/census_areas_TCD.geojson' using driver `GeoJSON'
Writing 18919 features with 32 fields and geometry type Multi Polygon.


**END**